In [ ]:
import pandas as pd
from IPython.display import clear_output, Markdown, Math
import ipywidgets as widgets
import os

----
## file input stuff:

* replace `test.txt` with yout whatsapp log file

In [ ]:
%%bash
./whatsapp2csv.sh test.txt

* read table `test.csv` exported by `whatsapp2csv.sh`

In [ ]:
messages = pd.read_csv('test.txt.csv', delimiter='\t')
messages.head()

* read emoji-data (can be found here: https://www.unicode.org/Public/emoji/11.0/emoji-data.txt) and generate a table file out of it

In [ ]:
%%bash
if [ ! -e emoji-data.txt ]
then
    echo "downloading emoji specification"
    wget https://www.unicode.org/Public/emoji/11.0/emoji-data.txt
else
    echo "found existing emoji specification"
fi


In [ ]:
emoji_blacklist = set([
    0x1F3FB,
    0x1F3FC,
    0x1F3FD,
    0x1F3FE,
    0x1F3FF
])

In [ ]:
emoji_data = pd.read_csv('emoji-data.txt', delimiter=';', comment='#', names=["unicode","type"])
emoji_data['type'] = emoji_data['type'].str.strip()
emoji_data = emoji_data[emoji_data['type'] == "Emoji_Presentation"]
emoji_data

* now build a set out of the unicode types

In [ ]:
ord("😀") == int('0x1f600',16)

In [ ]:
emoji_codes = emoji_data['unicode']
emoji_codes.head()

* we have to iterate over the whole list and extract all given ranges:

In [ ]:
emoji_code_list = []
for entry in emoji_codes:
    # testing whether we have an entry or a range:
    if '.' in entry:
        # range
        a,b = entry.split("..")
        for i in range(int(a,16),int(b,16) +1):
            if i not in emoji_blacklist:
                emoji_code_list.append(i)
    else:
        # single entry
        if i not in emoji_blacklist:
            emoji_code_list.append(int(entry,16))
emoji_code_set = set(emoji_code_list)

In [ ]:
# simple test:
print(ord("😀") in emoji_code_set, ord("a") in emoji_code_set)

* expanding column and fill new emojis

In [ ]:
messages["emojis"] = None

In [ ]:
for i in messages.index:
    emoji_list = []
    to_remove = []
    m = messages.iloc[i]['message']
    for c in str(m):
        if ord(c) in emoji_code_set:
            emoji_list.append(c)
        elif ord(c) in emoji_blacklist:
            to_remove.append(c)
            
    messages.loc[i,'emojis'] = emoji_list
    #remove emiójis from message
    for e in (emoji_list + to_remove):
        m = m.replace(e,"")
    messages.loc[i,'message'] = m


In [ ]:
messages[:20]

* get a list only containing messaged with emojis

In [ ]:
emoji_messages = messages[[True if len(e) > 0 else False for e in messages['emojis']]]
emoji_messages = emoji_messages[emoji_messages['message'] != ""]

In [ ]:
display(emoji_messages)

----
## learning part

In [ ]:
import numpy as np
import itertools
import sklearn.utils as sku
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer, HashingVectorizer
from sklearn.model_selection import train_test_split

In [ ]:
labels=[e[-1] for e in emoji_messages['emojis']]

In [ ]:
labels[:10]

In [ ]:
X1, Xt1, y1, yt1 = train_test_split(emoji_messages['message'], labels, test_size=0.1, random_state=4222)

In [ ]:
vectorizer = TfidfVectorizer(stop_words='english')
vec_train = vectorizer.fit_transform(X1)
vec_test = vectorizer.transform(Xt1)

In [ ]:
from sklearn.ensemble import RandomForestClassifier as RFC
from sklearn.neural_network import MLPClassifier as MLP
from sklearn.naive_bayes import MultinomialNB as MNB
#clf_a = RFC(criterion='entropy', random_state=4222)
clf_a = MLP()
clf_a.fit(vec_train, y1)

In [ ]:
pred = clf_a.predict(vectorizer.transform(Xt1))


In [ ]:
testlist = pd.DataFrame({'message': Xt1, 'pred': pred, 'trained': yt1})
testlist = pd.merge(testlist, emoji_messages['emojis'].to_frame(), left_index=True, right_index=True)
testlist.to_csv('export.csv')
testlist

In [ ]:
display(clf_a.predict(vectorizer.transform(["Boah Caner"]))[0])

In [ ]:
print(chr(0x1F3F))

In [ ]:
vec_train[0]

In [ ]:

out = widgets.Output()

t = widgets.Text()
b = widgets.Button(
    description='get smiley',
    disabled=False,
    button_style='', # 'success', 'info', 'warning', 'danger' or ''
    tooltip='Click me',
    icon='check'
)



def handle_submit(sender):
    with out:
        clear_output()
    with out:
        display(Markdown("# " + str(clf_a.predict(vectorizer.transform([t.value]))[0])))

b.on_click(handle_submit)
    
display(t)
display(widgets.VBox([b, out]))  